In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import requests
import bs4 as bs
import urllib.request

### Extracting features of the 2022 Movies from the Wikipedia

In [2]:
link = 'https://en.wikipedia.org/wiki/List_of_American_films_of_2022'

In [3]:
source = urllib.request.urlopen(link).read()
soup = bs.BeautifulSoup(source , 'lxml')

In [4]:
tables = soup.find_all('table' , class_='wikitable sortable')

In [5]:
df1 = pd.read_html(str(tables[0]))[0]
df2 = pd.read_html(str(tables[1]))[0]
df3 = pd.read_html(str(tables[2]))[0]
df4 = pd.read_html(str(tables[3]).replace("'1\"\'",'"1"'))[0] # avoided "ValueError: invalid literal for int() with base 10: '1"'

In [6]:
df = df1.append(df2.append(df3.append(df4 , ignore_index=True) , ignore_index=True) , ignore_index=True)

In [7]:
df

Opening  Opening.1                     Title  \
0     JANUARY        7.0                   The 355   
1     JANUARY        7.0  The Legend of La Llorona   
2     JANUARY        7.0              The Commando   
3     JANUARY        7.0            American Siege   
4     JANUARY       14.0                    Scream   
..        ...        ...                       ...   
313  DECEMBER       30.0            Alice, Darling   
314  DECEMBER        NaN                       NaN   
315  DECEMBER        NaN                       NaN   
316  DECEMBER        NaN                       NaN   
317  DECEMBER        NaN                       NaN   

                                    Production company  \
0    Universal Pictures / Freckle Films / FilmNatio...   
1                       Saban Films / Ageless Pictures   
2                 Saban Films / Premiere Entertainment   
3                               Vertical Entertainment   
4    Paramount Pictures / Spyglass Media Group / Ra...   
..                                                 ...   
313                     Lionsgate / Elevation Pictures   
314                                                NaN   
315                                                NaN   
316                                                NaN   
317                                                NaN   

                                         Cast and crew  \
0    Simon Kinberg (director/screenplay); Theresa R...   
1    Patricia Harris Seeley (director); José Prende...   
2    Asif Akbar (director); Koji Steven Sakai (scre...   
3    Edward John Drake (director/screenplay); Timot...   
4    Matt Bettinelli-Olpin, Tyler Gillett (director...   
..                                                 ...   
313  Mary Nighy (director); Alanna Francis (screenp...   
314                                                NaN   
315                                                NaN   
316                                                NaN   
317                                                NaN   

    .mw-parser-output .tooltip-dotted{border-bottom:1px dotted;cursor:help}Ref.  \
0                                                  [2]                            
1                                                  [3]                            
2                                                  [4]                            
3                                                  [5]                            
4                                                  [6]                            
..                                                 ...                            
313                                                NaN                            
314                                                NaN                            
315                                                NaN                            
316                                                NaN                            
317                                                NaN                            

      Ref.  
0      NaN  
1      NaN  
2      NaN  
3      NaN  
4      NaN  
..     ...  
313  [261]  
314    NaN  
315    NaN  
316    NaN  
317    NaN  

[318 rows x 7 columns]

In [8]:
df_2022 = df[['Title' , 'Cast and crew']]

In [9]:
df_2022

Title  \
0                     The 355   
1    The Legend of La Llorona   
2                The Commando   
3              American Siege   
4                      Scream   
..                        ...   
313            Alice, Darling   
314                       NaN   
315                       NaN   
316                       NaN   
317                       NaN   

                                         Cast and crew  
0    Simon Kinberg (director/screenplay); Theresa R...  
1    Patricia Harris Seeley (director); José Prende...  
2    Asif Akbar (director); Koji Steven Sakai (scre...  
3    Edward John Drake (director/screenplay); Timot...  
4    Matt Bettinelli-Olpin, Tyler Gillett (director...  
..                                                 ...  
313  Mary Nighy (director); Alanna Francis (screenp...  
314                                                NaN  
315                                                NaN  
316                                                NaN  
317                                                NaN  

[318 rows x 2 columns]

In [10]:
df_2022 = df_2022.dropna(how='any')

In [11]:
df_2022

Title  \
0                                         The 355   
1                        The Legend of La Llorona   
2                                    The Commando   
3                                  American Siege   
4                                          Scream   
..                                            ...   
309  Whitney Houston: I Wanna Dance with Somebody   
310                             The Pale Blue Eye   
311                                 Women Talking   
312                             A Man Called Otto   
313                                Alice, Darling   

                                         Cast and crew  
0    Simon Kinberg (director/screenplay); Theresa R...  
1    Patricia Harris Seeley (director); José Prende...  
2    Asif Akbar (director); Koji Steven Sakai (scre...  
3    Edward John Drake (director/screenplay); Timot...  
4    Matt Bettinelli-Olpin, Tyler Gillett (director...  
..                                                 ...  
309  Kasi Lemmons (director); Anthony McCarten (scr...  
310  Scott Cooper (director/screenplay); Christian ...  
311  Sarah Polley (director/screenplay); Rooney Mar...  
312  Marc Forster (director), David Magee (screenpl...  
313  Mary Nighy (director); Alanna Francis (screenp...  

[314 rows x 2 columns]

In [12]:
df_2022.isna().sum()

Title            0
Cast and crew    0
dtype: int64

In [13]:
from tmdbv3api import TMDb
import json
import requests
tmdb = TMDb()
tmdb.api_key = 'fce0af3409e6113c9b3c75aaf49341bb'

In [14]:
from tmdbv3api import Movie
tmdb_movie = Movie() 
def get_genre(x):
    genres = []
    try:
        result = tmdb_movie.search(x)
        print(f"Search result for '{x}': {result}")  # Debug print
        if not result:
            print("No results found.")
            return np.NaN
        else:
            movie = result[0]
            print(f"First movie in result: {movie}")  # Debug print
            movie_id = getattr(movie, 'id', None)
            if movie_id:
                response = requests.get(f'https://api.themoviedb.org/3/movie/{movie_id}?api_key={tmdb.api_key}')
                data_json = response.json()
                print(f"API response for movie ID {movie_id}: {data_json}")  # Debug print
                if 'genres' in data_json and data_json['genres']:
                    genre_str = " "
                    for genre in data_json['genres']:
                        genres.append(genre['name'])
                    return genre_str.join(genres)
                else:
                    print("No genres found in movie data.")
                    return np.NaN
            else:
                print("No movie ID found.")
                return np.NaN
    except Exception as e:
        print(f"An error occurred: {e}")
        return np.NaN

# Assuming df_2020 is your DataFrame and 'Title' is the column name
df_2022['genres'] = df_2022['Title'].map(lambda x: get_genre(str(x)))

Search result for 'The 355': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/dEE5tjmrxf4xrKrTnyghLsPSt6f.jpg', 'genre_ids': [28, 12, 53], 'id': 522016, 'original_language': 'en', 'original_title': 'The 355', 'overview': 'A group of top female agents from American, British, Chinese, Colombian, and German government agencies are drawn together to try and stop an organization from acquiring a deadly weapon to send the world into chaos.', 'popularity': 40.199, 'poster_path': '/zxizwEPE8jhpbMgrFbwCztgvh2m.jpg', 'release_date': '2022-01-05', 'title': 'The 355', 'video': False, 'vote_average': 6.1, 'vote_count': 963}], 'total_pages': 1, 'total_results': 1}
First movie in result: {'adult': False, 'backdrop_path': '/dEE5tjmrxf4xrKrTnyghLsPSt6f.jpg', 'genre_ids': [28, 12, 53], 'id': 522016, 'original_language': 'en', 'original_title': 'The 355', 'overview': 'A group of top female agents from American, British, Chinese, Colombian, and German government agencies are drawn together to t

Search result for 'American Siege': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/vsN9Lpi3HQJHQeHx8GzN6qfOYqk.jpg', 'genre_ids': [28, 12, 53], 'id': 766907, 'original_language': 'en', 'original_title': 'American Siege', 'overview': 'An ex-NYPD officer-turned-sheriff of a small rural Georgia town has to contend with a gang of thieves who have taken a wealthy doctor hostage.', 'popularity': 62.184, 'poster_path': '/daeVrgyj0ue8qb3AHyU3UeCwoZz.jpg', 'release_date': '2022-01-07', 'title': 'American Siege', 'video': False, 'vote_average': 5.403, 'vote_count': 146}, {'adult': False, 'backdrop_path': '/9yPojPY2WGbo3ORT7zCy0IHZ72n.jpg', 'genre_ids': [18], 'id': 14040, 'original_language': 'en', 'original_title': 'American Flyers', 'overview': "When Dr. Marcus Sommers realizes that he and his troubled, estranged brother David may be prone a fatal brain disease that runs in their family, he decides to make peace with his sibling, and invites him on a trip to the Rockies. There, the

API response for movie ID 585083: {'adult': False, 'backdrop_path': '/ep1urICLqtwwV1sTPHP9WXV4Uto.jpg', 'belongs_to_collection': {'id': 185103, 'name': 'Hotel Transylvania Collection', 'poster_path': '/9nR1xIcDo84gbbNZeFb9NCZYTdw.jpg', 'backdrop_path': '/5MJt6g7k9gADQH4xHn5mOEMa3Vr.jpg'}, 'budget': 75000000, 'genres': [{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}, {'id': 12, 'name': 'Adventure'}, {'id': 14, 'name': 'Fantasy'}], 'homepage': 'https://www.hoteltmovie.com', 'id': 585083, 'imdb_id': 'tt9848626', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Hotel Transylvania: Transformania', 'overview': 'When Van Helsing\'s mysterious invention, the "Monsterfication Ray," goes haywire, Drac and his monster pals are all transformed into humans, and Johnny becomes a monster. In their new mismatched bodies, Drac and Johnny must team up and race across the globe to find a cure before it\'s too late, and before they dri

Search result for 'The Royal Treatment': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/on1p1AdcfxmlyHhVXoycWt75D8H.jpg', 'genre_ids': [10749, 35], 'id': 790142, 'original_language': 'en', 'original_title': 'The Royal Treatment', 'overview': 'Isabella runs her own salon and isn’t afraid to speak her mind, while Prince Thomas runs his own country and is about to marry for duty rather than love. When Izzy and her fellow stylists get the opportunity of a lifetime to do the hair for the royal wedding, she and Prince Thomas learn that taking control of their own destiny requires following their hearts.', 'popularity': 11.647, 'poster_path': '/mYAv0YUoXJzLxIdEirOken8Quwf.jpg', 'release_date': '2022-01-20', 'title': 'The Royal Treatment', 'video': False, 'vote_average': 6.669, 'vote_count': 750}], 'total_pages': 1, 'total_results': 1}
First movie in result: {'adult': False, 'backdrop_path': '/on1p1AdcfxmlyHhVXoycWt75D8H.jpg', 'genre_ids': [10749, 35], 'id': 790142, 'original_lang

Search result for 'The Tiger Rising': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/dixceUg5veb5cl55DTEwTWDxCXU.jpg', 'genre_ids': [12, 10751, 18], 'id': 793269, 'original_language': 'en', 'original_title': 'The Tiger Rising', 'overview': 'When 12-year-old Rob Horton discovers a caged tiger in the woods near his home, his imagination runs wild and life begins to change in the most unexpected ways. With the help of a wise and mysterious maid, Willie May  and the stubborn new girl in school, he must navigate through childhood memories, heartache, and wondrous adventures.', 'popularity': 13.593, 'poster_path': '/mEukzqPoCpbrXLGslT8qdTuyRKZ.jpg', 'release_date': '2022-01-07', 'title': 'The Tiger Rising', 'video': False, 'vote_average': 5.4, 'vote_count': 29}, {'adult': False, 'backdrop_path': '/6tdr4b6N831sonGMaxiyAugfPc3.jpg', 'genre_ids': [28, 16, 878], 'id': 258807, 'original_language': 'ja', 'original_title': '劇場版 TIGER & BUNNY -The Rising-', 'overview': "The heroes of 'T

...

Search result for 'The Mean One': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/lzhoqccJ8b8qjRyT0fNbqKOCTLa.jpg', 'genre_ids': [27, 35], 'id': 1033052, 'original_language': 'en', 'original_title': 'The Mean One', 'overview': 'In a sleepy mountain town, Cindy witnesses the murder of her parents by a blood-thirsty green figure in a red Santa suit. Twenty years later, the Christmas-hating monster begins to terrorize the town once more. Cindy finds new purpose in stopping the creature and saving the holiday.', 'popularity': 12.094, 'poster_path': '/x2HLrgmwMqZi5ez7aXlSYGzXLy9.jpg', 'release_date': '2022-12-08', 'title': 'The Mean One', 'video': False, 'vote_average': 6.847, 'vote_count': 59}, {'adult': False, 'backdrop_path': None, 'genre_ids': [16], 'id': 1248403, 'original_language': 'pl', 'original_title': 'Co raz to na zawsze', 'overview': '"Once Means Forever" is a short animated film, which shows us, without delusion, story of young women. Girl who could be any other wo

Search result for 'Babylon': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/5fxTB08O7CW1hAcN2MWOKodp1h1.jpg', 'genre_ids': [18, 35], 'id': 615777, 'original_language': 'en', 'original_title': 'Babylon', 'overview': "A tale of outsized ambition and outrageous excess, tracing the rise and fall of multiple characters in an era of unbridled decadence and depravity during Hollywood's transition from silent films to sound films in the late 1920s.", 'popularity': 134.395, 'poster_path': '/wjOHjWCUE0YzDiEzKv8AfqHj3ir.jpg', 'release_date': '2022-12-22', 'title': 'Babylon', 'video': False, 'vote_average': 7.408, 'vote_count': 2881}, {'adult': False, 'backdrop_path': '/jAvwoSR1IZZM8cZz5zmXPmLwzfG.jpg', 'genre_ids': [18], 'id': 57082, 'original_language': 'en', 'original_title': 'Babylon', 'overview': 'Drama telling the story of Blue, a young man of Jamaican descent living in Brixton in 1980, as he hangs out with his friends, fronts a dub sound system, loses his job, struggles with fa

Search result for 'Whitney Houston: I Wanna Dance with Somebody': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/AcKPLFva3hnfdsArF5bcPTESVCo.jpg', 'genre_ids': [10402, 36, 18], 'id': 696157, 'original_language': 'en', 'original_title': 'Whitney Houston: I Wanna Dance with Somebody', 'overview': 'The joyous, emotional, heartbreaking celebration of the life and music of Whitney Houston, the greatest female R&B pop vocalist of all time. Tracking her journey from obscurity to musical superstardom.', 'popularity': 21.846, 'poster_path': '/oodPJ3Op1pWBhnEFyw5fampRCWf.jpg', 'release_date': '2022-12-20', 'title': 'Whitney Houston: I Wanna Dance with Somebody', 'video': False, 'vote_average': 7.0, 'vote_count': 394}, {'adult': False, 'backdrop_path': None, 'genre_ids': {}, 'id': 1040037, 'original_language': 'en', 'original_title': 'Whitney Houston: I Wanna Dance With Somebody', 'overview': '01. I Wanna Dance With Somebody\r 02. All The Man That I Need\r 03. Revelation\r 04. How Wi

API response for movie ID 777245: {'adult': False, 'backdrop_path': '/edH2sKM63YiSEOWoaJPN87a71dZ.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}], 'homepage': 'https://www.mgmstudios.com/women-talking', 'id': 777245, 'imdb_id': 'tt13669038', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Women Talking', 'overview': "A group of women in an isolated religious colony struggle to reconcile their faith with a series of sexual assaults committed by the colony's men.", 'popularity': 31.074, 'poster_path': '/wcTc9GveMMjAdHSlzdE0FaRCtqi.jpg', 'production_companies': [{'id': 81, 'logo_path': '/8wOfUhA7vwU2gbPjQy7Vv3EiF0o.png', 'name': 'Plan B Entertainment', 'origin_country': 'US'}, {'id': 114777, 'logo_path': None, 'name': 'Hear/Say Productions', 'origin_country': 'US'}, {'id': 41, 'logo_path': '/xAot4SSOIHiWQ2WEnVXYGR1lce9.png', 'name': 'Orion Pictures', 'origin_country': 'US'}], 'production_countries': [{'iso_3166_1': 'US', 'n

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [15]:
df_2022

Title  \
0                                         The 355   
1                        The Legend of La Llorona   
2                                    The Commando   
3                                  American Siege   
4                                          Scream   
..                                            ...   
309  Whitney Houston: I Wanna Dance with Somebody   
310                             The Pale Blue Eye   
311                                 Women Talking   
312                             A Man Called Otto   
313                                Alice, Darling   

                                         Cast and crew  \
0    Simon Kinberg (director/screenplay); Theresa R...   
1    Patricia Harris Seeley (director); José Prende...   
2    Asif Akbar (director); Koji Steven Sakai (scre...   
3    Edward John Drake (director/screenplay); Timot...   
4    Matt Bettinelli-Olpin, Tyler Gillett (director...   
..                                                 ...   
309  Kasi Lemmons (director); Anthony McCarten (scr...   
310  Scott Cooper (director/screenplay); Christian ...   
311  Sarah Polley (director/screenplay); Rooney Mar...   
312  Marc Forster (director), David Magee (screenpl...   
313  Mary Nighy (director); Alanna Francis (screenp...   

                              genres  
0          Action Adventure Thriller  
1    Family Animation Fantasy Horror  
2              Action Crime Thriller  
3          Action Adventure Thriller  
4            Horror Mystery Thriller  
..                               ...  
309              Music History Drama  
310    Thriller Crime Horror Mystery  
311                            Drama  
312                     Comedy Drama  
313           Thriller Drama Romance  

[314 rows x 3 columns]

In [16]:
df_2022.isna().sum()

Title            0
Cast and crew    0
genres           1
dtype: int64

In [17]:
def get_director(x):
    if " (director)" in x:
        return x.split(" (director)")[0]
    elif " (directors)" in x:
        return x.split(" (directors)")[0]
    else:
        return x.split(" (director/screenplay)")[0]

In [18]:
df_2022['director_name'] = df_2022['Cast and crew'].map(lambda x: get_director(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [19]:
df_2022['director_name']

0                             Simon Kinberg
1                    Patricia Harris Seeley
2                                Asif Akbar
3                         Edward John Drake
4      Matt Bettinelli-Olpin, Tyler Gillett
                       ...                 
309                            Kasi Lemmons
310                            Scott Cooper
311                            Sarah Polley
312                            Marc Forster
313                              Mary Nighy
Name: director_name, Length: 314, dtype: object

In [20]:
def get_actor1(x):
    return ((x.split("screenplay); ")[-1]).split(", ")[0])

In [21]:
df_2022['actor_1_name'] = df_2022['Cast and crew'].map(lambda x: get_actor1(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [22]:
df_2022['actor_1_name']

0       Jessica Chastain
1          Autumn Reeser
2          Mickey Rourke
3      Timothy V. Murphy
4        Melissa Barrera
             ...        
309          Naomi Ackie
310       Christian Bale
311          Rooney Mara
312            Tom Hanks
313        Anna Kendrick
Name: actor_1_name, Length: 314, dtype: object

In [23]:
def get_actor2(x):
    if len((x.split("screenplay); ")[-1]).split(", ")) < 2:
        return np.NaN
    else:
        return ((x.split("screenplay); ")[-1]).split(", ")[1])

In [24]:
df_2022['actor_2_name'] = df_2022['Cast and crew'].map(lambda x: get_actor2(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [25]:
df_2022['actor_2_name']

0          Penélope Cruz
1            Danny Trejo
2      Michael Jai White
3           Bruce Willis
4          Mason Gooding
             ...        
309        Stanley Tucci
310        Harry Melling
311           Claire Foy
312      Mariana Treviño
313      Kaniehtiio Horn
Name: actor_2_name, Length: 314, dtype: object

In [26]:
def get_actor3(x):
    if len((x.split("screenplay); ")[-1]).split(", ")) < 3:
        return np.NaN
    else:
        return ((x.split("screenplay); ")[-1]).split(", ")[2])

In [27]:
df_2022['actor_3_name'] = df_2022['Cast and crew'].map(lambda x: get_actor3(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [28]:
df_2022['actor_3_name']

0          Fan Bingbing
1          Antonio Cupo
2                   NaN
3             Rob Gough
4          Jenna Ortega
             ...       
309      Ashton Sanders
310    Gillian Anderson
311      Jessie Buckley
312       Rachel Keller
313     Charlie Carrick
Name: actor_3_name, Length: 314, dtype: object

In [29]:
df_2022

Title  \
0                                         The 355   
1                        The Legend of La Llorona   
2                                    The Commando   
3                                  American Siege   
4                                          Scream   
..                                            ...   
309  Whitney Houston: I Wanna Dance with Somebody   
310                             The Pale Blue Eye   
311                                 Women Talking   
312                             A Man Called Otto   
313                                Alice, Darling   

                                         Cast and crew  \
0    Simon Kinberg (director/screenplay); Theresa R...   
1    Patricia Harris Seeley (director); José Prende...   
2    Asif Akbar (director); Koji Steven Sakai (scre...   
3    Edward John Drake (director/screenplay); Timot...   
4    Matt Bettinelli-Olpin, Tyler Gillett (director...   
..                                                 ...   
309  Kasi Lemmons (director); Anthony McCarten (scr...   
310  Scott Cooper (director/screenplay); Christian ...   
311  Sarah Polley (director/screenplay); Rooney Mar...   
312  Marc Forster (director), David Magee (screenpl...   
313  Mary Nighy (director); Alanna Francis (screenp...   

                              genres                         director_name  \
0          Action Adventure Thriller                         Simon Kinberg   
1    Family Animation Fantasy Horror                Patricia Harris Seeley   
2              Action Crime Thriller                            Asif Akbar   
3          Action Adventure Thriller                     Edward John Drake   
4            Horror Mystery Thriller  Matt Bettinelli-Olpin, Tyler Gillett   
..                               ...                                   ...   
309              Music History Drama                          Kasi Lemmons   
310    Thriller Crime Horror Mystery                          Scott Cooper   
311                            Drama                          Sarah Polley   
312                     Comedy Drama                          Marc Forster   
313           Thriller Drama Romance                            Mary Nighy   

          actor_1_name       actor_2_name      actor_3_name  
0     Jessica Chastain      Penélope Cruz      Fan Bingbing  
1        Autumn Reeser        Danny Trejo      Antonio Cupo  
2        Mickey Rourke  Michael Jai White               NaN  
3    Timothy V. Murphy       Bruce Willis         Rob Gough  
4      Melissa Barrera      Mason Gooding      Jenna Ortega  
..                 ...                ...               ...  
309        Naomi Ackie      Stanley Tucci    Ashton Sanders  
310     Christian Bale      Harry Melling  Gillian Anderson  
311        Rooney Mara         Claire Foy    Jessie Buckley  
312          Tom Hanks    Mariana Treviño     Rachel Keller  
313      Anna Kendrick    Kaniehtiio Horn   Charlie Carrick  

[314 rows x 7 columns]

In [30]:
df_2022 = df_2022.rename(columns={'Title' : 'movie_title'})

In [31]:
newdf_2022 = df_2022.loc[: , ['director_name' , 'actor_1_name' , 'actor_2_name' , 'actor_3_name' , 'genres' , 'movie_title']]

In [32]:
newdf_2022

director_name       actor_1_name  \
0                           Simon Kinberg   Jessica Chastain   
1                  Patricia Harris Seeley      Autumn Reeser   
2                              Asif Akbar      Mickey Rourke   
3                       Edward John Drake  Timothy V. Murphy   
4    Matt Bettinelli-Olpin, Tyler Gillett    Melissa Barrera   
..                                    ...                ...   
309                          Kasi Lemmons        Naomi Ackie   
310                          Scott Cooper     Christian Bale   
311                          Sarah Polley        Rooney Mara   
312                          Marc Forster          Tom Hanks   
313                            Mary Nighy      Anna Kendrick   

          actor_2_name      actor_3_name                           genres  \
0        Penélope Cruz      Fan Bingbing        Action Adventure Thriller   
1          Danny Trejo      Antonio Cupo  Family Animation Fantasy Horror   
2    Michael Jai White               NaN            Action Crime Thriller   
3         Bruce Willis         Rob Gough        Action Adventure Thriller   
4        Mason Gooding      Jenna Ortega          Horror Mystery Thriller   
..                 ...               ...                              ...   
309      Stanley Tucci    Ashton Sanders              Music History Drama   
310      Harry Melling  Gillian Anderson    Thriller Crime Horror Mystery   
311         Claire Foy    Jessie Buckley                            Drama   
312    Mariana Treviño     Rachel Keller                     Comedy Drama   
313    Kaniehtiio Horn   Charlie Carrick           Thriller Drama Romance   

                                      movie_title  
0                                         The 355  
1                        The Legend of La Llorona  
2                                    The Commando  
3                                  American Siege  
4                                          Scream  
..                                            ...  
309  Whitney Houston: I Wanna Dance with Somebody  
310                             The Pale Blue Eye  
311                                 Women Talking  
312                             A Man Called Otto  
313                                Alice, Darling  

[314 rows x 6 columns]

In [33]:
newdf_2022['actor_1_name'] = newdf_2022['actor_1_name'].replace(np.nan , 'unknown')
newdf_2022['actor_2_name'] = newdf_2022['actor_2_name'].replace(np.nan , 'unknown')
newdf_2022['actor_3_name'] = newdf_2022['actor_3_name'].replace(np.nan , 'unknown')

In [34]:
newdf_2022['movie_title'] = newdf_2022['movie_title'].str.lower()

In [35]:
newdf_2022['comb'] = newdf_2022['actor_1_name'] + ' ' + newdf_2022['actor_2_name'] + ' ' + newdf_2022['actor_3_name'] + ' ' + newdf_2022['director_name'] + ' ' + newdf_2022['genres']

In [36]:
newdf_2022

director_name       actor_1_name  \
0                           Simon Kinberg   Jessica Chastain   
1                  Patricia Harris Seeley      Autumn Reeser   
2                              Asif Akbar      Mickey Rourke   
3                       Edward John Drake  Timothy V. Murphy   
4    Matt Bettinelli-Olpin, Tyler Gillett    Melissa Barrera   
..                                    ...                ...   
309                          Kasi Lemmons        Naomi Ackie   
310                          Scott Cooper     Christian Bale   
311                          Sarah Polley        Rooney Mara   
312                          Marc Forster          Tom Hanks   
313                            Mary Nighy      Anna Kendrick   

          actor_2_name      actor_3_name                           genres  \
0        Penélope Cruz      Fan Bingbing        Action Adventure Thriller   
1          Danny Trejo      Antonio Cupo  Family Animation Fantasy Horror   
2    Michael Jai White           unknown            Action Crime Thriller   
3         Bruce Willis         Rob Gough        Action Adventure Thriller   
4        Mason Gooding      Jenna Ortega          Horror Mystery Thriller   
..                 ...               ...                              ...   
309      Stanley Tucci    Ashton Sanders              Music History Drama   
310      Harry Melling  Gillian Anderson    Thriller Crime Horror Mystery   
311         Claire Foy    Jessie Buckley                            Drama   
312    Mariana Treviño     Rachel Keller                     Comedy Drama   
313    Kaniehtiio Horn   Charlie Carrick           Thriller Drama Romance   

                                      movie_title  \
0                                         the 355   
1                        the legend of la llorona   
2                                    the commando   
3                                  american siege   
4                                          scream   
..                                            ...   
309  whitney houston: i wanna dance with somebody   
310                             the pale blue eye   
311                                 women talking   
312                             a man called otto   
313                                alice, darling   

                                                  comb  
0    Jessica Chastain Penélope Cruz Fan Bingbing Si...  
1    Autumn Reeser Danny Trejo Antonio Cupo Patrici...  
2    Mickey Rourke Michael Jai White unknown Asif A...  
3    Timothy V. Murphy Bruce Willis Rob Gough Edwar...  
4    Melissa Barrera Mason Gooding Jenna Ortega Mat...  
..                                                 ...  
309  Naomi Ackie Stanley Tucci Ashton Sanders Kasi ...  
310  Christian Bale Harry Melling Gillian Anderson ...  
311  Rooney Mara Claire Foy Jessie Buckley Sarah Po...  
312  Tom Hanks Mariana Treviño Rachel Keller Marc F...  
313  Anna Kendrick Kaniehtiio Horn Charlie Carrick ...  

[314 rows x 7 columns]

In [37]:
newdf_2022.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           1
movie_title      0
comb             1
dtype: int64

In [38]:
newdf_2022 = newdf_2022.dropna(how='any')

In [39]:
newdf_2022

director_name       actor_1_name  \
0                           Simon Kinberg   Jessica Chastain   
1                  Patricia Harris Seeley      Autumn Reeser   
2                              Asif Akbar      Mickey Rourke   
3                       Edward John Drake  Timothy V. Murphy   
4    Matt Bettinelli-Olpin, Tyler Gillett    Melissa Barrera   
..                                    ...                ...   
309                          Kasi Lemmons        Naomi Ackie   
310                          Scott Cooper     Christian Bale   
311                          Sarah Polley        Rooney Mara   
312                          Marc Forster          Tom Hanks   
313                            Mary Nighy      Anna Kendrick   

          actor_2_name      actor_3_name                           genres  \
0        Penélope Cruz      Fan Bingbing        Action Adventure Thriller   
1          Danny Trejo      Antonio Cupo  Family Animation Fantasy Horror   
2    Michael Jai White           unknown            Action Crime Thriller   
3         Bruce Willis         Rob Gough        Action Adventure Thriller   
4        Mason Gooding      Jenna Ortega          Horror Mystery Thriller   
..                 ...               ...                              ...   
309      Stanley Tucci    Ashton Sanders              Music History Drama   
310      Harry Melling  Gillian Anderson    Thriller Crime Horror Mystery   
311         Claire Foy    Jessie Buckley                            Drama   
312    Mariana Treviño     Rachel Keller                     Comedy Drama   
313    Kaniehtiio Horn   Charlie Carrick           Thriller Drama Romance   

                                      movie_title  \
0                                         the 355   
1                        the legend of la llorona   
2                                    the commando   
3                                  american siege   
4                                          scream   
..                                            ...   
309  whitney houston: i wanna dance with somebody   
310                             the pale blue eye   
311                                 women talking   
312                             a man called otto   
313                                alice, darling   

                                                  comb  
0    Jessica Chastain Penélope Cruz Fan Bingbing Si...  
1    Autumn Reeser Danny Trejo Antonio Cupo Patrici...  
2    Mickey Rourke Michael Jai White unknown Asif A...  
3    Timothy V. Murphy Bruce Willis Rob Gough Edwar...  
4    Melissa Barrera Mason Gooding Jenna Ortega Mat...  
..                                                 ...  
309  Naomi Ackie Stanley Tucci Ashton Sanders Kasi ...  
310  Christian Bale Harry Melling Gillian Anderson ...  
311  Rooney Mara Claire Foy Jessie Buckley Sarah Po...  
312  Tom Hanks Mariana Treviño Rachel Keller Marc F...  
313  Anna Kendrick Kaniehtiio Horn Charlie Carrick ...  

[313 rows x 7 columns]

In [40]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import requests
import bs4 as bs
import urllib.request

### Extracting Features of the 2023 Movies from the Wikipedia

In [41]:
link = 'https://en.wikipedia.org/wiki/List_of_American_films_of_2023'

In [42]:
source = urllib.request.urlopen(link).read()
soup = bs.BeautifulSoup(source , 'lxml')

In [43]:
tables = soup.find_all('table' , class_='wikitable sortable')

In [44]:
df1 = pd.read_html(str(tables[0]))[0]
df2 = pd.read_html(str(tables[1]))[0]
df3 = pd.read_html(str(tables[2]))[0]
df4 = pd.read_html(str(tables[3]).replace("'1\"\'",'"1"'))[0] # avoided "ValueError: invalid literal for int() with base 10: '1"'

In [45]:
df = df1.append(df2.append(df3.append(df4 , ignore_index=True) , ignore_index=True) , ignore_index=True)

In [46]:
df

Opening  Opening.1                 Title  \
0     JANUARY          6                 M3GAN   
1     JANUARY          6           The Old Way   
2     JANUARY         11  The Devil Conspiracy   
3     JANUARY         13                 Plane   
4     JANUARY         13           House Party   
..        ...        ...                   ...   
339  DECEMBER         22                Memory   
340  DECEMBER         25      The Color Purple   
341  DECEMBER         25  The Boys in the Boat   
342  DECEMBER         25               Ferrari   
343  DECEMBER         29            Good Grief   

                                    Production company  \
0    Universal Pictures / Blumhouse Productions / A...   
1                           Saban Films / Saturn Films   
2                                 Samuel Goldwyn Films   
3    Lionsgate / MadRiver Pictures / Di Bonaventura...   
4              Warner Bros. Pictures / New Line Cinema   
..                                                 ...   
339                       Ketchup Entertainment / Mubi   
340  Warner Bros. Pictures / Amblin Entertainment /...   
341          Metro-Goldwyn-Mayer / Smokehouse Pictures   
342            Neon / STXfilms / Ketchup Entertainment   
343                                            Netflix   

                                         Cast and crew   Ref.  
0    Gerard Johnstone (director); Akela Cooper (scr...    [3]  
1    Brett Donowho (director); Carl W. Lucas (scree...    [4]  
2    Nathan Frankowski (director); Ed Alan (screenp...    [5]  
3    Jean-François Richet (director); Charles Cummi...    [6]  
4    Calmatic (director); Jamal Olori, Stephen Glov...    [7]  
..                                                 ...    ...  
339  Michel Franco (director/screenplay); Jessica C...  [326]  
340  Blitz Bazawule (director), Marcus Gardley (scr...  [327]  
341  George Clooney (director), Mark L. Smith (scre...  [328]  
342  Michael Mann (director), Troy Kennedy Martin (...  [329]  
343  Dan Levy (director/screenplay); Dan Levy, Ruth...  [330]  

[344 rows x 6 columns]

In [47]:
df_2023 = df[['Title' , 'Cast and crew']]

In [48]:
df_2023

Title                                      Cast and crew
0                   M3GAN  Gerard Johnstone (director); Akela Cooper (scr...
1             The Old Way  Brett Donowho (director); Carl W. Lucas (scree...
2    The Devil Conspiracy  Nathan Frankowski (director); Ed Alan (screenp...
3                   Plane  Jean-François Richet (director); Charles Cummi...
4             House Party  Calmatic (director); Jamal Olori, Stephen Glov...
..                    ...                                                ...
339                Memory  Michel Franco (director/screenplay); Jessica C...
340      The Color Purple  Blitz Bazawule (director), Marcus Gardley (scr...
341  The Boys in the Boat  George Clooney (director), Mark L. Smith (scre...
342               Ferrari  Michael Mann (director), Troy Kennedy Martin (...
343            Good Grief  Dan Levy (director/screenplay); Dan Levy, Ruth...

[344 rows x 2 columns]

In [49]:
df_2023.isna().sum()

Title            0
Cast and crew    0
dtype: int64

In [50]:
from tmdbv3api import TMDb
import json
import requests
tmdb = TMDb()
tmdb.api_key = 'fce0af3409e6113c9b3c75aaf49341bb'

In [51]:
from tmdbv3api import Movie
tmdb_movie = Movie() 
def get_genre(x):
    genres = []
    try:
        result = tmdb_movie.search(x)
        print(f"Search result for '{x}': {result}")  # Debug print
        if not result:
            print("No results found.")
            return np.NaN
        else:
            movie = result[0]
            print(f"First movie in result: {movie}")  # Debug print
            movie_id = getattr(movie, 'id', None)
            if movie_id:
                response = requests.get(f'https://api.themoviedb.org/3/movie/{movie_id}?api_key={tmdb.api_key}')
                data_json = response.json()
                print(f"API response for movie ID {movie_id}: {data_json}")  # Debug print
                if 'genres' in data_json and data_json['genres']:
                    genre_str = " "
                    for genre in data_json['genres']:
                        genres.append(genre['name'])
                    return genre_str.join(genres)
                else:
                    print("No genres found in movie data.")
                    return np.NaN
            else:
                print("No movie ID found.")
                return np.NaN
    except Exception as e:
        print(f"An error occurred: {e}")
        return np.NaN

# Assuming df_2020 is your DataFrame and 'Title' is the column name
df_2023['genres'] = df_2023['Title'].map(lambda x: get_genre(str(x)))

Search result for 'M3GAN': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/4iYfKsWtKLsy18SOL9egydL91ok.jpg', 'genre_ids': [878, 27], 'id': 536554, 'original_language': 'en', 'original_title': 'M3GAN', 'overview': "A brilliant toy company roboticist uses artificial intelligence to develop M3GAN, a life-like doll programmed to emotionally bond with her newly orphaned niece. But when the doll's programming works too well, she becomes overprotective of her new friend with terrifying results.", 'popularity': 79.757, 'poster_path': '/d9nBoowhjiiYc4FBNtQkPY7c11H.jpg', 'release_date': '2022-12-28', 'title': 'M3GAN', 'video': False, 'vote_average': 7.091, 'vote_count': 3844}, {'adult': False, 'backdrop_path': None, 'genre_ids': [878, 27], 'id': 1071585, 'original_language': 'en', 'original_title': 'M3GAN 2.0', 'overview': '', 'popularity': 11.117, 'poster_path': '/tVdTOWt21vo5GB6tjd65qmPmqIr.jpg', 'release_date': '2025-06-26', 'title': 'M3GAN 2.0', 'video': False, 'vote_average': 0.

API response for movie ID 872954: {'adult': False, 'backdrop_path': '/7tXJhpWe4iEWzWad6DkH9iPpR8b.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 37, 'name': 'Western'}, {'id': 18, 'name': 'Drama'}], 'homepage': '', 'id': 872954, 'imdb_id': 'tt8593824', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'The Old Way', 'overview': 'An old gunslinger and his daughter must face the consequences of his past, when the son of a man he killed years ago arrives to take his revenge.', 'popularity': 22.939, 'poster_path': '/8HCCYAIocXxMKn7J9yQfDX1vBM5.jpg', 'production_companies': [{'id': 186482, 'logo_path': '/bgT1Zj009TyAhG4MaSfstlidzmA.png', 'name': 'Intercut Capital', 'origin_country': 'US'}, {'id': 831, 'logo_path': '/vLENXiYTyITnMDrTKabUXhgTKX2.png', 'name': 'Saturn Films', 'origin_country': 'US'}, {'id': 19995, 'logo_path': '/50TlgnTTuESDGK8k5qyffSAP3UP.png', 'name': 'Tri-Fold Pictures', 'origin_country': 'US'}, {'id': 70142, 'logo_path': '/trW549hP

API response for movie ID 646389: {'adult': False, 'backdrop_path': '/6JU2ysRVOHqav0Hs6BUv4mvvDxZ.jpg', 'belongs_to_collection': {'id': 1099094, 'name': 'Plane Collection', 'poster_path': '/65sSXSZr4CXKYGbMyxWJASzBt6E.jpg', 'backdrop_path': None}, 'budget': 25000000, 'genres': [{'id': 28, 'name': 'Action'}], 'homepage': 'https://www.plane.movie', 'id': 646389, 'imdb_id': 'tt5884796', 'origin_country': ['GB'], 'original_language': 'en', 'original_title': 'Plane', 'overview': 'After a heroic job of successfully landing his storm-damaged aircraft in a war zone, a fearless pilot finds himself between the agendas of multiple militias planning to take the plane and its passengers hostage.', 'popularity': 86.239, 'poster_path': '/oJRsTQR47pyjSJCZYpOfbycpNBR.jpg', 'production_companies': [{'id': 73492, 'logo_path': '/bQzrYnomE5hIRJMxEy7e2SCYew3.png', 'name': 'MadRiver Pictures', 'origin_country': 'US'}, {'id': 435, 'logo_path': '/AjzK0s2w1GtLfR4hqCjVSYi0Sr8.png', 'name': 'di Bonaventura Pictur

Search result for 'Sick': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/ve3RLbCSuUKA02OZJ5F0fMmXVMn.jpg', 'genre_ids': [27, 9648, 53], 'id': 829410, 'original_language': 'en', 'original_title': 'Sick', 'overview': "While quarantining at her family's lake house during the pandemic, Parker and her best friend are threatened by an unexpected visitor.", 'popularity': 34.047, 'poster_path': '/bshCGAHZRldAfdxXDX3637PW9cR.jpg', 'release_date': '2022-09-11', 'title': 'Sick', 'video': False, 'vote_average': 6.2, 'vote_count': 241}, {'adult': False, 'backdrop_path': '/yg46KK8VrgBBz8FrgGdMfQ3t9p0.jpg', 'genre_ids': [878, 27], 'id': 308867, 'original_language': 'en', 'original_title': 'Sick', 'overview': 'Two years into the outbreak, SICK roam the land and the remaining survivors struggle day-to-day trying to rebuild civilization. With the SICK more active at night time, three people need to seek shelter in an empty home.', 'popularity': 3.223, 'poster_path': '/gksOfYdr0tgRHuMA0kyVBX

API response for movie ID 154400: {'adult': False, 'backdrop_path': '/jDNXIth0TlZcz3sBMJdMx7JjIZf.jpg', 'belongs_to_collection': None, 'budget': 12600000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 80, 'name': 'Crime'}], 'homepage': '', 'id': 154400, 'imdb_id': 'tt1600196', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'The Drop', 'overview': "Bob Saginowski finds himself at the center of a robbery gone awry and entwined in an investigation that digs deep into the neighborhood's past where friends, families, and foes all work together to make a living - no matter the cost.", 'popularity': 60.034, 'poster_path': '/ehFOkPH0tRdbyghxGDR418Mgn9V.jpg', 'production_companies': [{'id': 43, 'logo_path': '/4RgIPr55kBakgupWkzdDxqXJEqr.png', 'name': 'Fox Searchlight Pictures', 'origin_country': 'US'}, {'id': 7076, 'logo_path': '/8BFxn9NUWSgp0ndih569Gm62xiC.png', 'name': 'Chernin Entertainment', 'origin_country': 'US'}, {'id': 22213, 'logo_path': '/qx9K6bFWJupwde0xQDwOv

...

API response for movie ID 1025491: {'adult': False, 'backdrop_path': '/zxNAQeptsUIY53zdtvqqro0CgyB.jpg', 'belongs_to_collection': None, 'budget': 10000000, 'genres': [{'id': 18, 'name': 'Drama'}], 'homepage': 'https://www.sonyclassics.com/film/freudslastsession/', 'id': 1025491, 'imdb_id': 'tt20420628', 'origin_country': ['US', 'GB', 'IE'], 'original_language': 'en', 'original_title': "Freud's Last Session", 'overview': 'On the eve of the Second World War, two of the greatest minds of the twentieth century, C.S. Lewis and Sigmund Freud converge for their own personal battle over the existence of God. The film interweaves the lives of Freud and Lewis, past, present, and through fantasy, bursting from the confines of Freud’s study on a dynamic journey.', 'popularity': 21.678, 'poster_path': '/mp7IBxFuvNZSVOOGESybvaPxd7y.jpg', 'production_companies': [{'id': 20782, 'logo_path': '/tTfJjcJHmVPBbPv3q1ATtaX5mFf.png', 'name': 'WestEnd Films', 'origin_country': 'GB'}, {'id': 141391, 'logo_path'

Search result for 'The Color Purple': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/rSle4ix2IZ6UMgCDY8L3ngdOmSZ.jpg', 'genre_ids': [18], 'id': 558915, 'original_language': 'en', 'original_title': 'The Color Purple', 'overview': "A decades-spanning tale of love and resilience and of one woman's journey to independence. Celie faces many hardships in her life, but ultimately finds extraordinary strength and hope in the unbreakable bonds of sisterhood.", 'popularity': 38.776, 'poster_path': '/h5bqIxM8GO4TewJ0u6Rzkg58ssJ.jpg', 'release_date': '2023-12-25', 'title': 'The Color Purple', 'video': False, 'vote_average': 7.045, 'vote_count': 233}, {'adult': False, 'backdrop_path': '/rhMpAPvoy1beXd8gA6CvYoCSztj.jpg', 'genre_ids': [18, 36], 'id': 873, 'original_language': 'en', 'original_title': 'The Color Purple', 'overview': "An epic tale spanning forty years in the life of Celie, an African-American woman living in the South who survives incredible abuse and bigotry. After Celie's

API response for movie ID 823452: {'adult': False, 'backdrop_path': '/mHpoCdCSebNDIIHbqaAxbD57o7H.jpg', 'belongs_to_collection': None, 'budget': 40000000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 36, 'name': 'History'}], 'homepage': 'https://www.mgm.com/movies/the-boys-in-the-boat', 'id': 823452, 'imdb_id': 'tt1856080', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'The Boys in the Boat', 'overview': "The triumphant underdog story of the University of Washington men's rowing team, who stunned the world by competing at the 1936 Berlin Olympics.", 'popularity': 28.88, 'poster_path': '/ncJMztHprw3gLRAnDjNnnT23CIt.jpg', 'production_companies': [{'id': 1782, 'logo_path': '/d1mlUfuG0NoQ4x0C7bK80wLGWA1.png', 'name': 'Smoke House Pictures', 'origin_country': 'US'}, {'id': 21, 'logo_path': '/usUnaYV6hQnlVAXP6r4HwrlLFPG.png', 'name': 'Metro-Goldwyn-Mayer', 'origin_country': 'US'}, {'id': 143790, 'logo_path': '/wo1smiXdiwwxai2dwJlRiGwE7rS.png', 'name': 'Spyglass Med

API response for movie ID 365620: {'adult': False, 'backdrop_path': '/du11oPPbEoDnUpiREO5tUg47rJd.jpg', 'belongs_to_collection': None, 'budget': 95000000, 'genres': [{'id': 36, 'name': 'History'}, {'id': 18, 'name': 'Drama'}], 'homepage': 'https://www.ferrari-film.com/', 'id': 365620, 'imdb_id': 'tt3758542', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Ferrari', 'overview': 'Set during the summer of 1957. Ex-racecar driver, Enzo Ferrari, is in crisis. Bankruptcy stalks the company he and his wife, Laura, built from nothing ten years earlier. Their tempestuous marriage struggles with the mourning for one son and the acknowledgement of another.', 'popularity': 65.206, 'poster_path': '/LyCOcGqOTyTmaXu2TK8LfGveIb.jpg', 'production_companies': [{'id': 47729, 'logo_path': '/bAxh897TGgdR0Py6wdd0UuE147Z.png', 'name': 'STXfilms', 'origin_country': 'US'}, {'id': 675, 'logo_path': '/fy7laY9J4tbYz7yNxGEKmoMrXRt.png', 'name': 'Forward Pass', 'origin_country': 'US'}, {'id'

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [52]:
df_2023['genres']

0                       Science Fiction Horror
1                                Western Drama
2      Horror Fantasy Science Fiction Thriller
3                                       Action
4                                       Comedy
                        ...                   
339                      Action Thriller Crime
340                                      Drama
341                              Drama History
342                              History Drama
343                               Comedy Drama
Name: genres, Length: 344, dtype: object

In [53]:
df_2023

Title                                      Cast and crew  \
0                   M3GAN  Gerard Johnstone (director); Akela Cooper (scr...   
1             The Old Way  Brett Donowho (director); Carl W. Lucas (scree...   
2    The Devil Conspiracy  Nathan Frankowski (director); Ed Alan (screenp...   
3                   Plane  Jean-François Richet (director); Charles Cummi...   
4             House Party  Calmatic (director); Jamal Olori, Stephen Glov...   
..                    ...                                                ...   
339                Memory  Michel Franco (director/screenplay); Jessica C...   
340      The Color Purple  Blitz Bazawule (director), Marcus Gardley (scr...   
341  The Boys in the Boat  George Clooney (director), Mark L. Smith (scre...   
342               Ferrari  Michael Mann (director), Troy Kennedy Martin (...   
343            Good Grief  Dan Levy (director/screenplay); Dan Levy, Ruth...   

                                      genres  
0                     Science Fiction Horror  
1                              Western Drama  
2    Horror Fantasy Science Fiction Thriller  
3                                     Action  
4                                     Comedy  
..                                       ...  
339                    Action Thriller Crime  
340                                    Drama  
341                            Drama History  
342                            History Drama  
343                             Comedy Drama  

[344 rows x 3 columns]

In [54]:
df_2023.isna().sum()

Title            0
Cast and crew    0
genres           0
dtype: int64

In [55]:
df_2023['director_name'] = df['Cast and crew'].map(lambda x: get_director(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [56]:
df_2023['director_name']

0          Gerard Johnstone
1             Brett Donowho
2         Nathan Frankowski
3      Jean-François Richet
4                  Calmatic
               ...         
339           Michel Franco
340          Blitz Bazawule
341          George Clooney
342            Michael Mann
343                Dan Levy
Name: director_name, Length: 344, dtype: object

In [57]:
df_2023['actor_1_name'] = df_2023['Cast and crew'].map(lambda x: get_actor1(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [58]:
df_2023['actor_1_name']

0      Allison Williams
1          Nicolas Cage
2       Alice Orr-Ewing
3         Gerard Butler
4            Tosin Cole
             ...       
339    Jessica Chastain
340    Fantasia Barrino
341       Callum Turner
342         Adam Driver
343            Dan Levy
Name: actor_1_name, Length: 344, dtype: object

In [59]:
df_2023['actor_2_name'] = df_2023['Cast and crew'].map(lambda x: get_actor2(x))

In [60]:
df_2023['actor_2_name']

0             Violet McGraw
1      Ryan Kiera Armstrong
2                 Joe Doyle
3               Mike Colter
4            Jacob Latimore
               ...         
339         Peter Sarsgaard
340        Taraji P. Henson
341           Joel Edgerton
342           Penelope Cruz
343              Ruth Negga
Name: actor_2_name, Length: 344, dtype: object

In [61]:
df_2023['actor_3_name'] = df_2023['Cast and crew'].map(lambda x: get_actor3(x))

In [62]:
df_2023['actor_3_name']

0           Amie Donald
1                   NaN
2          Eveline Hall
3              Yoson An
4          Karen Obilom
             ...       
339       Merritt Wever
340     Danielle Brooks
341      Peter Guinness
342    Shailene Woodley
343        Himesh Patel
Name: actor_3_name, Length: 344, dtype: object

In [63]:
df_2023

Title                                      Cast and crew  \
0                   M3GAN  Gerard Johnstone (director); Akela Cooper (scr...   
1             The Old Way  Brett Donowho (director); Carl W. Lucas (scree...   
2    The Devil Conspiracy  Nathan Frankowski (director); Ed Alan (screenp...   
3                   Plane  Jean-François Richet (director); Charles Cummi...   
4             House Party  Calmatic (director); Jamal Olori, Stephen Glov...   
..                    ...                                                ...   
339                Memory  Michel Franco (director/screenplay); Jessica C...   
340      The Color Purple  Blitz Bazawule (director), Marcus Gardley (scr...   
341  The Boys in the Boat  George Clooney (director), Mark L. Smith (scre...   
342               Ferrari  Michael Mann (director), Troy Kennedy Martin (...   
343            Good Grief  Dan Levy (director/screenplay); Dan Levy, Ruth...   

                                      genres         director_name  \
0                     Science Fiction Horror      Gerard Johnstone   
1                              Western Drama         Brett Donowho   
2    Horror Fantasy Science Fiction Thriller     Nathan Frankowski   
3                                     Action  Jean-François Richet   
4                                     Comedy              Calmatic   
..                                       ...                   ...   
339                    Action Thriller Crime         Michel Franco   
340                                    Drama        Blitz Bazawule   
341                            Drama History        George Clooney   
342                            History Drama          Michael Mann   
343                             Comedy Drama              Dan Levy   

         actor_1_name          actor_2_name      actor_3_name  
0    Allison Williams         Violet McGraw       Amie Donald  
1        Nicolas Cage  Ryan Kiera Armstrong               NaN  
2     Alice Orr-Ewing             Joe Doyle      Eveline Hall  
3       Gerard Butler           Mike Colter          Yoson An  
4          Tosin Cole        Jacob Latimore      Karen Obilom  
..                ...                   ...               ...  
339  Jessica Chastain       Peter Sarsgaard     Merritt Wever  
340  Fantasia Barrino      Taraji P. Henson   Danielle Brooks  
341     Callum Turner         Joel Edgerton    Peter Guinness  
342       Adam Driver         Penelope Cruz  Shailene Woodley  
343          Dan Levy            Ruth Negga      Himesh Patel  

[344 rows x 7 columns]

In [64]:
df_2023 = df_2023.rename(columns={'Title':'movie_title'})

In [65]:
newdf_2023 = df_2023.loc[: , ['director_name' , 'actor_1_name' , 'actor_2_name' , 'actor_3_name' , 'genres' , 'movie_title']]

In [66]:
newdf_2023

director_name      actor_1_name          actor_2_name  \
0        Gerard Johnstone  Allison Williams         Violet McGraw   
1           Brett Donowho      Nicolas Cage  Ryan Kiera Armstrong   
2       Nathan Frankowski   Alice Orr-Ewing             Joe Doyle   
3    Jean-François Richet     Gerard Butler           Mike Colter   
4                Calmatic        Tosin Cole        Jacob Latimore   
..                    ...               ...                   ...   
339         Michel Franco  Jessica Chastain       Peter Sarsgaard   
340        Blitz Bazawule  Fantasia Barrino      Taraji P. Henson   
341        George Clooney     Callum Turner         Joel Edgerton   
342          Michael Mann       Adam Driver         Penelope Cruz   
343              Dan Levy          Dan Levy            Ruth Negga   

         actor_3_name                                   genres  \
0         Amie Donald                   Science Fiction Horror   
1                 NaN                            Western Drama   
2        Eveline Hall  Horror Fantasy Science Fiction Thriller   
3            Yoson An                                   Action   
4        Karen Obilom                                   Comedy   
..                ...                                      ...   
339     Merritt Wever                    Action Thriller Crime   
340   Danielle Brooks                                    Drama   
341    Peter Guinness                            Drama History   
342  Shailene Woodley                            History Drama   
343      Himesh Patel                             Comedy Drama   

              movie_title  
0                   M3GAN  
1             The Old Way  
2    The Devil Conspiracy  
3                   Plane  
4             House Party  
..                    ...  
339                Memory  
340      The Color Purple  
341  The Boys in the Boat  
342               Ferrari  
343            Good Grief  

[344 rows x 6 columns]

In [67]:
newdf_2023['actor_1_name'] = newdf_2023['actor_1_name'].replace(np.nan , 'unknown')
newdf_2023['actor_2_name'] = newdf_2023['actor_2_name'].replace(np.nan , 'unknown')
newdf_2023['actor_3_name'] = newdf_2023['actor_3_name'].replace(np.nan , 'unknown')

In [68]:
newdf_2023['movie_title'] = newdf_2023['movie_title'].str.lower()

In [69]:
newdf_2023['comb'] = newdf_2023['actor_1_name'] + ' ' + newdf_2023['actor_2_name'] + ' ' + newdf_2023['actor_3_name'] + ' ' + newdf_2023['director_name'] + ' ' + newdf_2023['genres'] 

In [70]:
newdf_2023

director_name      actor_1_name          actor_2_name  \
0        Gerard Johnstone  Allison Williams         Violet McGraw   
1           Brett Donowho      Nicolas Cage  Ryan Kiera Armstrong   
2       Nathan Frankowski   Alice Orr-Ewing             Joe Doyle   
3    Jean-François Richet     Gerard Butler           Mike Colter   
4                Calmatic        Tosin Cole        Jacob Latimore   
..                    ...               ...                   ...   
339         Michel Franco  Jessica Chastain       Peter Sarsgaard   
340        Blitz Bazawule  Fantasia Barrino      Taraji P. Henson   
341        George Clooney     Callum Turner         Joel Edgerton   
342          Michael Mann       Adam Driver         Penelope Cruz   
343              Dan Levy          Dan Levy            Ruth Negga   

         actor_3_name                                   genres  \
0         Amie Donald                   Science Fiction Horror   
1             unknown                            Western Drama   
2        Eveline Hall  Horror Fantasy Science Fiction Thriller   
3            Yoson An                                   Action   
4        Karen Obilom                                   Comedy   
..                ...                                      ...   
339     Merritt Wever                    Action Thriller Crime   
340   Danielle Brooks                                    Drama   
341    Peter Guinness                            Drama History   
342  Shailene Woodley                            History Drama   
343      Himesh Patel                             Comedy Drama   

              movie_title                                               comb  
0                   m3gan  Allison Williams Violet McGraw Amie Donald Ger...  
1             the old way  Nicolas Cage Ryan Kiera Armstrong unknown Bret...  
2    the devil conspiracy  Alice Orr-Ewing Joe Doyle Eveline Hall Nathan ...  
3                   plane  Gerard Butler Mike Colter Yoson An Jean-Franço...  
4             house party  Tosin Cole Jacob Latimore Karen Obilom Calmati...  
..                    ...                                                ...  
339                memory  Jessica Chastain Peter Sarsgaard Merritt Wever...  
340      the color purple  Fantasia Barrino Taraji P. Henson Danielle Bro...  
341  the boys in the boat  Callum Turner Joel Edgerton Peter Guinness Geo...  
342               ferrari  Adam Driver Penelope Cruz Shailene Woodley Mic...  
343            good grief  Dan Levy Ruth Negga Himesh Patel Dan Levy Come...  

[344 rows x 7 columns]

In [71]:
newdf_2023.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [72]:
my_df = newdf_2022.append(newdf_2023 , ignore_index=True)

In [73]:
my_df

director_name       actor_1_name  \
0                           Simon Kinberg   Jessica Chastain   
1                  Patricia Harris Seeley      Autumn Reeser   
2                              Asif Akbar      Mickey Rourke   
3                       Edward John Drake  Timothy V. Murphy   
4    Matt Bettinelli-Olpin, Tyler Gillett    Melissa Barrera   
..                                    ...                ...   
652                         Michel Franco   Jessica Chastain   
653                        Blitz Bazawule   Fantasia Barrino   
654                        George Clooney      Callum Turner   
655                          Michael Mann        Adam Driver   
656                              Dan Levy           Dan Levy   

          actor_2_name      actor_3_name                           genres  \
0        Penélope Cruz      Fan Bingbing        Action Adventure Thriller   
1          Danny Trejo      Antonio Cupo  Family Animation Fantasy Horror   
2    Michael Jai White           unknown            Action Crime Thriller   
3         Bruce Willis         Rob Gough        Action Adventure Thriller   
4        Mason Gooding      Jenna Ortega          Horror Mystery Thriller   
..                 ...               ...                              ...   
652    Peter Sarsgaard     Merritt Wever            Action Thriller Crime   
653   Taraji P. Henson   Danielle Brooks                            Drama   
654      Joel Edgerton    Peter Guinness                    Drama History   
655      Penelope Cruz  Shailene Woodley                    History Drama   
656         Ruth Negga      Himesh Patel                     Comedy Drama   

                  movie_title  \
0                     the 355   
1    the legend of la llorona   
2                the commando   
3              american siege   
4                      scream   
..                        ...   
652                    memory   
653          the color purple   
654      the boys in the boat   
655                   ferrari   
656                good grief   

                                                  comb  
0    Jessica Chastain Penélope Cruz Fan Bingbing Si...  
1    Autumn Reeser Danny Trejo Antonio Cupo Patrici...  
2    Mickey Rourke Michael Jai White unknown Asif A...  
3    Timothy V. Murphy Bruce Willis Rob Gough Edwar...  
4    Melissa Barrera Mason Gooding Jenna Ortega Mat...  
..                                                 ...  
652  Jessica Chastain Peter Sarsgaard Merritt Wever...  
653  Fantasia Barrino Taraji P. Henson Danielle Bro...  
654  Callum Turner Joel Edgerton Peter Guinness Geo...  
655  Adam Driver Penelope Cruz Shailene Woodley Mic...  
656  Dan Levy Ruth Negga Himesh Patel Dan Levy Come...  

[657 rows x 7 columns]

In [74]:
old_df = pd.read_csv('final_1.csv')

In [75]:
old_df

director_name  \
0                                         James Cameron   
1                                        Gore Verbinski   
2                                            Sam Mendes   
3                                     Christopher Nolan   
4                                           Doug Walker   
...                                                 ...   
6439                                     Matthew Vaughn   
6440                                          Joel Coen   
6441                                  Denzel Washington   
6442                                     Erwin brothers   
6443  Apichatpong Weerasethakul (director/acreenplay...   

                                           actor_1_name       actor_2_name  \
0                                           CCH Pounder   Joel David Moore   
1                                           Johnny Depp      Orlando Bloom   
2                                       Christoph Waltz       Rory Kinnear   
3                                             Tom Hardy     Christian Bale   
4                                           Doug Walker         Rob Walker   
...                                                 ...                ...   
6439                                      Ralph Fiennes     Gemma Arterton   
6440                                  Denzel Washington  Frances McDormand   
6441                                  Michael B. Jordan       Chanté Adams   
6442                                       Zachary Levi        Anna Paquin   
6443  Apichatpong Weerasethakul (director/acreenplay...         Elkin Díaz   

              actor_3_name                            genres  \
0                Wes Studi   Action Adventure Fantasy Sci-Fi   
1           Jack Davenport          Action Adventure Fantasy   
2         Stephanie Sigman         Action Adventure Thriller   
3     Joseph Gordon-Levitt                   Action Thriller   
4                  unknown                       Documentary   
...                    ...                               ...   
6439            Rhys Ifans  Action Comedy Adventure Thriller   
6440         Bertie Carvel                         Drama War   
6441       Jalon Christian                     Drama Romance   
6442          Dennis Quaid                             Drama   
6443        Jeanne Balibar     Drama Science Fiction Mystery   

                                            movie_title  \
0                                                avatar   
1              pirates of the caribbean: at world's end   
2                                               spectre   
3                                 the dark knight rises   
4     star wars: episode vii - the force awakens    ...   
...                                                 ...   
6439                                     the king's man   
6440                             the tragedy of macbeth   
6441                               a journal for jordan   
6442                                  american underdog   
6443                                            memoria   

                                                   comb  
0     CCH Pounder Joel David Moore Wes Studi James C...  
1     Johnny Depp Orlando Bloom Jack Davenport Gore ...  
2     Christoph Waltz Rory Kinnear Stephanie Sigman ...  
3     Tom Hardy Christian Bale Joseph Gordon-Levitt ...  
4     Doug Walker Rob Walker unknown Doug Walker Doc...  
...                                                 ...  
6439  Ralph Fiennes Gemma Arterton Rhys Ifans Matthe...  
6440  Denzel Washington Frances McDormand Bertie Car...  
6441  Michael B. Jordan Chanté Adams Jalon Christian...  
6442  Zachary Levi Anna Paquin Dennis Quaid Erwin br...  
6443  Apichatpong Weerasethakul (director/acreenplay...  

[6444 rows x 7 columns]

In [76]:
newdf_2023.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [77]:
old_df.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [78]:
final_df = old_df.append(my_df , ignore_index=True)

In [79]:
final_df

director_name      actor_1_name      actor_2_name  \
0         James Cameron       CCH Pounder  Joel David Moore   
1        Gore Verbinski       Johnny Depp     Orlando Bloom   
2            Sam Mendes   Christoph Waltz      Rory Kinnear   
3     Christopher Nolan         Tom Hardy    Christian Bale   
4           Doug Walker       Doug Walker        Rob Walker   
...                 ...               ...               ...   
7096      Michel Franco  Jessica Chastain   Peter Sarsgaard   
7097     Blitz Bazawule  Fantasia Barrino  Taraji P. Henson   
7098     George Clooney     Callum Turner     Joel Edgerton   
7099       Michael Mann       Adam Driver     Penelope Cruz   
7100           Dan Levy          Dan Levy        Ruth Negga   

              actor_3_name                           genres  \
0                Wes Studi  Action Adventure Fantasy Sci-Fi   
1           Jack Davenport         Action Adventure Fantasy   
2         Stephanie Sigman        Action Adventure Thriller   
3     Joseph Gordon-Levitt                  Action Thriller   
4                  unknown                      Documentary   
...                    ...                              ...   
7096         Merritt Wever            Action Thriller Crime   
7097       Danielle Brooks                            Drama   
7098        Peter Guinness                    Drama History   
7099      Shailene Woodley                    History Drama   
7100          Himesh Patel                     Comedy Drama   

                                            movie_title  \
0                                                avatar   
1              pirates of the caribbean: at world's end   
2                                               spectre   
3                                 the dark knight rises   
4     star wars: episode vii - the force awakens    ...   
...                                                 ...   
7096                                             memory   
7097                                   the color purple   
7098                               the boys in the boat   
7099                                            ferrari   
7100                                         good grief   

                                                   comb  
0     CCH Pounder Joel David Moore Wes Studi James C...  
1     Johnny Depp Orlando Bloom Jack Davenport Gore ...  
2     Christoph Waltz Rory Kinnear Stephanie Sigman ...  
3     Tom Hardy Christian Bale Joseph Gordon-Levitt ...  
4     Doug Walker Rob Walker unknown Doug Walker Doc...  
...                                                 ...  
7096  Jessica Chastain Peter Sarsgaard Merritt Wever...  
7097  Fantasia Barrino Taraji P. Henson Danielle Bro...  
7098  Callum Turner Joel Edgerton Peter Guinness Geo...  
7099  Adam Driver Penelope Cruz Shailene Woodley Mic...  
7100  Dan Levy Ruth Negga Himesh Patel Dan Levy Come...  

[7101 rows x 7 columns]

In [80]:
final_df.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [81]:
final_df.to_csv('final_2.csv' , index=False)

PermissionError: [Errno 13] Permission denied: 'final_2.csv'